In [2]:

import warnings
warnings.filterwarnings('ignore')

In [6]:
import pandas as pd

# Specify the correct encoding explicitly
urls = pd.read_excel(r"C:\Users\filip\OneDrive\Desktop\IRONHACK\Final_Project\FragranceFusion\wiki_urls.xlsx")

urls

urls
0          A Fragrance Story
1              A Lab On Fire
2                 A. N Other
3        Abercrombie & Fitch
4     Above Average Humanity
...                      ...
1213                  3003BC
1214                    4711
1215                 d'Orsay
1216           pH Fragrances
1217                   Æmium

[1218 rows x 1 columns]

In [7]:
print(urls.columns)


Index(['urls'], dtype='object')


In [8]:
urls

urls
0          A Fragrance Story
1              A Lab On Fire
2                 A. N Other
3        Abercrombie & Fitch
4     Above Average Humanity
...                      ...
1213                  3003BC
1214                    4711
1215                 d'Orsay
1216           pH Fragrances
1217                   Æmium

[1218 rows x 1 columns]

In [9]:
from unidecode import unidecode

# Function to generate URL from brand name
def generate_url(brand_name):
    # Remove accents from brand name
    brand_name = unidecode(brand_name)
    # Convert brand name to lowercase
    brand_name = brand_name.lower()
    # Replace specific characters
    replacements = {
        '&': 'and',
        '(': '',
        ')': '',
        '#': 'sharp',
        '.': '',
        ' ': '-',
        "'": ''  # Remove apostrophe
    }
    for old, new in replacements.items():
        brand_name = brand_name.replace(old, new)
    # Generate URL
    url = f"https://www.wikiparfum.com/en/fragrances?filter-brand={brand_name}#catalogue"
    return url

# Convert all values in the 'urls' column to strings
urls['urls'] = urls['urls'].astype(str)

# Apply the function to create 'url' column
urls['urls'] = urls['urls'].apply(lambda x: generate_url(x) if x else '')

# Remove any duplicate URLs
urls.drop_duplicates(inplace=True)


In [11]:
brand_urls = urls

In [12]:
urls.to_csv('brand_urls.csv', index=False)

In [3]:
from selenium import webdriver
from selenium.webdriver.common.by import By
import pandas as pd

# Define a function to scrape href attributes starting with '/en/fragrances/'
def scrape_href(driver, url):
    driver.get(url)
    href_elements = driver.find_elements(By.XPATH, '//a[starts-with(@href, "/en/fragrances/")]')
    href_list = [element.get_attribute('href') for element in href_elements]
    return href_list

# Define the URL to scrape
url = "https://www.wikiparfum.com/en/fragrances?filter-brand=acqua-di-portofino#catalogue"

# Configure Chrome options to disable SSL verification
chrome_options = webdriver.ChromeOptions()
chrome_options.add_argument('--ignore-ssl-errors=yes')
chrome_options.add_argument('--ignore-certificate-errors')

# Initialize Selenium webdriver with Chrome options
driver = webdriver.Chrome(options=chrome_options)  # You may need to adjust this depending on your browser and setup

# Create an empty list to store scraped hrefs
scraped_hrefs = []

# Scrape hrefs from the specified URL
hrefs = scrape_href(driver, url)
scraped_hrefs.extend(hrefs)

# Close the webdriver
driver.quit()

# Save the scraped hrefs to a dataframe and CSV file
scraped_hrefs_df = pd.DataFrame(scraped_hrefs, columns=['href'])
scraped_hrefs_df.to_csv('scraped_hrefs_acqua_di_portofino.csv', index=False)



In [5]:
from selenium import webdriver
from selenium.webdriver.common.by import By
from selenium.common.exceptions import StaleElementReferenceException
import pandas as pd

# Define a function to scrape href attributes starting with '/en/fragrances/'
def scrape_href(driver, url):
    driver.get(url)
    try:
        href_elements = driver.find_elements(By.XPATH, '//a[starts-with(@href, "/en/fragrances/")]')
        href_list = [element.get_attribute('href') for element in href_elements]
        return href_list
    except StaleElementReferenceException:
        # Retry finding elements
        return scrape_href(driver, url)

# Define your dataframe with brand URLs
brand_urls_df = pd.read_csv('brand_urls.csv')  # Assuming you have a CSV file with a column named 'urls'

# Configure Chrome options to disable SSL verification
chrome_options = webdriver.ChromeOptions()
chrome_options.add_argument('--ignore-ssl-errors=yes')
chrome_options.add_argument('--ignore-certificate-errors')

# Initialize Selenium webdriver with Chrome options
driver = webdriver.Chrome(options=chrome_options)  # You may need to adjust this depending on your browser and setup

# Create an empty list to store scraped hrefs
scraped_hrefs = []

# Loop through each URL in your dataframe and scrape hrefs
for url in brand_urls_df['urls']:  # Change 'url' to 'urls'
    print("Scraping URL:", url)  # Print URL for debugging
    hrefs = scrape_href(driver, url)
    if hrefs:  # Check if hrefs list is not empty
        print("Found hrefs:", hrefs)  # Print found hrefs for debugging
        scraped_hrefs.extend(hrefs)
    else:
        print("No hrefs found for URL:", url)  # Print if no hrefs found for debugging

# Close the webdriver
driver.quit()

# Save the scraped hrefs to a dataframe and CSV file
scraped_hrefs_df = pd.DataFrame(scraped_hrefs, columns=['href'])
scraped_hrefs_df.to_csv('scraped_hrefs.csv', index=False)




Scraping URL: https://www.wikiparfum.com/en/fragrances?filter-brand=a-fragrance-story#catalogue
Found hrefs: ['https://www.wikiparfum.com/en/fragrances/wilde', 'https://www.wikiparfum.com/en/fragrances/wilde', 'https://www.wikiparfum.com/en/fragrances/o-feminin', 'https://www.wikiparfum.com/en/fragrances/o-feminin', 'https://www.wikiparfum.com/en/fragrances/miss-dior-parfum', 'https://www.wikiparfum.com/en/fragrances/miss-dior-parfum', 'https://www.wikiparfum.com/en/fragrances/wilde', 'https://www.wikiparfum.com/en/fragrances/wilde', 'https://www.wikiparfum.com/en/fragrances/o-feminin', 'https://www.wikiparfum.com/en/fragrances/o-feminin', 'https://www.wikiparfum.com/en/fragrances/miss-dior-parfum', 'https://www.wikiparfum.com/en/fragrances/miss-dior-parfum', 'https://www.wikiparfum.com/en/fragrances/la-vie-est-belle-rose-extraordinaire', 'https://www.wikiparfum.com/en/fragrances/la-vie-est-belle-rose-extraordinaire', 'https://www.wikiparfum.com/en/fragrances/karl-lagerfeld-pour-femme-

In [6]:
scraped_hrefs_df.duplicated().sum()

66377

In [7]:
scraped_hrefs_df = scraped_hrefs_df.drop_duplicates()

In [9]:
scraped_hrefs_df.to_csv('perfume_urls_final.csv', index = False)

In [10]:
import requests
from bs4 import BeautifulSoup
import time
time.sleep(1)  # Adding 1 second delay before making the next request

url= 'https://www.wikiparfum.com/en/fragrances/denim-original'


response = requests.get(url, verify=False)
response

c:\Users\filip\anaconda3\lib\site-packages\urllib3\connectionpool.py:1103: InsecureRequestWarning: Unverified HTTPS request is being made to host 'www.wikiparfum.com'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(


<Response [200]>

In [61]:
soup = BeautifulSoup(response.content, 'html.parser')

In [62]:
# Ingredients

spans = soup.find_all(class_="leading-relaxed text-black")

# Iterate over each span and extract the text inside
ingredients = [span.get_text() for span in spans]

unique_ingredients = list(set(ingredients))

unique_ingredients

['Amber',
 'Clary Sage',
 'Petitgrain',
 'Cedarwood',
 'Vetiver',
 'Bergamot',
 'Incense / Olibanum']

In [63]:
# Name 

# Assuming you have BeautifulSoup installed and 'soup' contains the parsed HTML

# Find the span element with the specified class
span_element = soup.find(class_="relative block")

# Extract the text and remove leading/trailing whitespace
name = span_element.text.strip()

print(name)




DENIM ORIGINAL


In [64]:
# Brand

# Assuming you have BeautifulSoup installed and 'soup' contains the parsed HTML

# Find the span element with the specified class
span_element = soup.find(class_="text-base font-primaryMedium md:text-bigger3")

# Extract the text
brand = span_element.get_text(strip=True)

print(brand)


Denim


In [65]:
# Classification

# Assuming you have BeautifulSoup installed and 'soup' contains the parsed HTML

# Find the div element with the specified class
div_element = soup.find(class_="flex items-center justify-between mt-6 mb-2 md:mt-5 md:mb-2 panoramic:mt-2 panoramic:mb-0")

# Extract the text
classification = div_element.get_text(strip=True)

print(classification)



Woody Amber Classical


In [66]:
# Family and subfamily


# Assuming you have BeautifulSoup installed and 'soup' contains the parsed HTML

# Find all h6 elements with the specified class
h6_elements = soup.find_all(class_="leading-tight font-primaryMedium text-darkGray text-small2 md:text-base")

# Extract the text from each h6 element
families = [h6.get_text(strip=True) for h6 in h6_elements]

# Use set to eliminate duplicates and then convert it back to a list
unique_families = list(set(families))

# Join the unique values with a comma
family_and_subfamily = ', '.join(unique_families)

print(family_and_subfamily)



WOODY, AMBERY (ORIENTAL)


In [69]:
# Description

# Assuming you have BeautifulSoup installed and 'soup' contains the parsed HTML

# Find the div element with the specified class
div_element = soup.find(class_="hidden md:block md:mb-14")

# Extract the text
description = div_element.get_text(strip=True)

print(description)


Denim Original is a fragrance for confident men. Its spicy and unusual floral texture makes this scent enticingly rich, complex and masculine.


In [11]:
perfumes = pd.read_csv(r"C:\Users\filip\OneDrive\Desktop\IRONHACK\Final_Project\FragranceFusion\perfume_urls_final.csv")
perfumes

href
0         https://www.wikiparfum.com/en/fragrances/wilde
1      https://www.wikiparfum.com/en/fragrances/o-fem...
2      https://www.wikiparfum.com/en/fragrances/miss-...
3      https://www.wikiparfum.com/en/fragrances/la-vi...
4      https://www.wikiparfum.com/en/fragrances/karl-...
...                                                  ...
10822  https://www.wikiparfum.com/en/fragrances/genet...
10823    https://www.wikiparfum.com/en/fragrances/hamaca
10824  https://www.wikiparfum.com/en/fragrances/wande...
10825  https://www.wikiparfum.com/en/fragrances/elixi...
10826   https://www.wikiparfum.com/en/fragrances/hashtag

[10827 rows x 1 columns]

In [12]:
# Assuming 'sample' is your DataFrame and 'Absolute URLs' is the column containing URLs
url_list = perfumes['href'].tolist()



In [13]:
import requests
from bs4 import BeautifulSoup
import pandas as pd

# Define functions for extracting information from the HTML

def extract_name(soup):
    span_element = soup.find(class_="relative block")
    return span_element.text.strip() if span_element else None

def extract_brand(soup):
    span_element = soup.find(class_="text-base font-primaryMedium md:text-bigger3")
    return span_element.get_text(strip=True) if span_element else None

def extract_ingredients(soup):
    spans = soup.find_all(class_="leading-relaxed text-black")
    ingredients = [span.get_text() for span in spans]
    unique_ingredients = list(set(ingredients))
    return ', '.join(unique_ingredients)

def extract_classification(soup):
    div_element = soup.find(class_="flex items-center justify-between mt-6 mb-2 md:mt-5 md:mb-2 panoramic:mt-2 panoramic:mb-0")
    return div_element.get_text(strip=True) if div_element else None

def extract_family_and_subfamily(soup):
    h6_elements = soup.find_all(class_="leading-tight font-primaryMedium text-darkGray text-small2 md:text-base")
    families = [h6.get_text(strip=True) for h6 in h6_elements]
    unique_families = list(set(families))
    return ', '.join(unique_families)

def extract_description(soup):
    div_element = soup.find(class_="hidden md:block md:mb-14")
    return div_element.get_text(strip=True) if div_element else None

# Function to scrape data from URLs and create DataFrame columns
def scrape_data(url_list):
    data = {'Absolute URLs': url_list}
    sample = pd.DataFrame(data)
    
    for index, row in sample.iterrows():
        url = row['Absolute URLs']
        response = requests.get(url, verify=False)  # Disable SSL verification
        soup = BeautifulSoup(response.content, 'html.parser')
        
        sample.at[index, 'Name'] = extract_name(soup)
        sample.at[index, 'Brand'] = extract_brand(soup)
        sample.at[index, 'Ingredients'] = extract_ingredients(soup)
        sample.at[index, 'Classification'] = extract_classification(soup)
        sample.at[index, 'Family_and_Subfamily'] = extract_family_and_subfamily(soup)
        sample.at[index, 'Description'] = extract_description(soup)
    
    return sample

# Assuming url_list contains the URLs

# Scrape data and create new DataFrame with extracted information
perfumes = scrape_data(url_list)




c:\Users\filip\anaconda3\lib\site-packages\urllib3\connectionpool.py:1103: InsecureRequestWarning: Unverified HTTPS request is being made to host 'www.wikiparfum.com'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(
c:\Users\filip\anaconda3\lib\site-packages\urllib3\connectionpool.py:1103: InsecureRequestWarning: Unverified HTTPS request is being made to host 'www.wikiparfum.com'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(
c:\Users\filip\anaconda3\lib\site-packages\urllib3\connectionpool.py:1103: InsecureRequestWarning: Unverified HTTPS request is being made to host 'www.wikiparfum.com'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(
c:\Users\filip\anaconda3\lib\site-packages\urllib

TypeError: 'DataFrame' object is not callable

In [14]:
from unidecode import unidecode

# Assuming df is your DataFrame
from unidecode import unidecode

# Assuming df is your DataFrame
perfumes['Name'] = perfumes['Name'].apply(lambda x: unidecode(x) if x is not None else x)
perfumes['Brand'] = perfumes['Brand'].apply(lambda x: unidecode(x) if x is not None else x)
perfumes['Ingredients'] = perfumes['Ingredients'].apply(lambda x: unidecode(x) if x is not None else x)
perfumes['Classification'] = perfumes['Classification'].apply(lambda x: unidecode(x) if x is not None else x)
perfumes['Family_and_Subfamily'] = perfumes['Family_and_Subfamily'].apply(lambda x: unidecode(x) if x is not None else x)
perfumes['Description'] = perfumes['Description'].apply(lambda x: unidecode(x) if x is not None else x)





perfumes.to_csv('perfumes_batch1.csv', index=False)